In [17]:
import pandas as pd
import requests
import io
import os
import numpy as np

# Data loading and processing

In [20]:
# Shuffle the dataset, and divide the dataset into 10 parts
with open(r"C:\Users\huyen\OneDrive\Documents\GitHub\CORD-19-KG\Data\all-final-cleaned-triples_3.csv", 'r', encoding = 'utf-8') as f:
    dataset = pd.read_csv(f)
# shuffle data
dataset = dataset.sample(frac=1, axis=1).reset_index(drop=True)
# divide data
subsets = np.array_split(dataset, 10)  
len(subsets)
for i in range(len(subsets)):
    data = subsets[:i+1]
    data_concat = pd.concat(data)
    with open(r"C:\Users\huyen\OneDrive\Documents\GitHub\CORD-19-KG\Data\all-final-cleaned-triple3-10sets\subset_{}.csv".format(i+1), 
              'w', encoding = 'utf-8', newline='') as f:
        data_concat.to_csv(f)

# Importing data into neo4j
 Done! Manually import in Neo4j interface       

# Retrieving

In [21]:
# !pip install neo4j
from neo4j import GraphDatabase

# uri = "bolt://localhost:7687"
# driver = GraphDatabase.driver(uri, auth=("neo4j", "Huyen123"))

class Neo4jConnection:
    
    def __init__(self, uri, user, pwd):
        self.__uri = uri
        self.__user = user
        self.__pwd = pwd
        self.__driver = None
        try:
            self.__driver = GraphDatabase.driver(self.__uri, auth=(self.__user, self.__pwd))
            print('connected successfully!!')
        except Exception as e:
            print("Failed to create the driver:", e)
        
    def close(self):
        if self.__driver is not None:
            self.__driver.close()
        
    def query(self, query, parameters=None, db=None):
        assert self.__driver is not None, "Driver not initialized!"
        session = None
        response = None
        try: 
            session = self.__driver.session(database=db) if db is not None else self.__driver.session() 
            response = list(session.run(query, parameters))
        except Exception as e:
            print("Query failed:", e)
        finally: 
            if session is not None:
                session.close()
        return response


        
conn = Neo4jConnection(uri="bolt://localhost:7687", 
                       user="neo4j",              
                       pwd="Huyen123")


connected successfully!!


In [11]:
# create a neo4j session in python
# session = driver.session()
def retrieval (conn):
    rel_types = [['gene_disease', 'disease_gene'], 
             ['disease_species', 'species_disease'],
             ['disease_symptom', 'symptom_disease'],
             ['disease_treat_procedure','treat_procedure_disease' ],
             ['drug_disease', 'disease_drug'],
             ['disease_disease']]  
    covid_variants = ['covid-19', 'coronavirus', 'sars-cov', 'sars', 'covs', 'severe acute respiratory syndrome']
    # Create query statements
    all_answs = {}
    for i,list_ in enumerate(rel_types):
        query_answ = []
        print('Query: {}--------{}-----------------'.format(i+1,list_))
        for rel in list_:
            query_statement = """MATCH (n)-[r:{}]->(m) where m.id in {} or n.id in {} RETURN n, m""".format(rel, covid_variants, covid_variants)
            output = conn.query(query_statement)
            for o in output:
                ent = (list(o[0].values()))    
                if ent[0] not in covid_variants:
                    query_answ.extend(ent)

        all_answs['query_%s' %i+1] = set(query_answ)
    return all_answs        


dir_path = 'C:\Users\huyen\OneDrive\Documents\GitHub\CORD-19-KG\Results\KG-output-neo4j'
isExist = os.path.exists(dir_path)


## For all data subsets




if not isExist:
    os.makedirs(dir_path)
for i in range(len(data_dict)): 
    print('i----------%s'%i)
    dir_s_path = 'C:\Users\huyen\OneDrive\Documents\GitHub\CORD-19-KG\Results\KG-output-neo4j\subset_
    isExist_s = os.path.exists(dir_s_path)
    if not isExist_s:
        dir = os.makedirs(dir_s_path)
    path = 'C:\Users\huyen\OneDrive\Documents\GitHub\CORD-19-KG\Results\KG-output-neo4j\subset_1\query_{}.csv'.format(i+1)
    df = pd.DataFrame(data_dict[], columns = [column_name])
    with open(path, encoding = 'utf-8', newline='') as f:
        df.to_csv(f)


Query: 1--------['gene_disease', 'disease_gene']-----------------
Query: 2--------['disease_species', 'species_disease']-----------------
Query: 3--------['disease_symptom', 'symptom_disease']-----------------
Query: 4--------['disease_treat_procedure', 'treat_procedure_disease']-----------------
Query: 5--------['drug_disease', 'disease_drug']-----------------
Query: 6--------['disease_disease']-----------------
{'query_1': ['toll', 'receptor', 'macrodomain', 'ace2', 'nl63', 'oc43', 'clone', 'sirna', 'protein e', 'coronavirus e protein', 'impact', 'hku1', 'antibody', 'light', 'ttsps', 'ace2', 'nl63', 'hong kong', 'pattern', 'papr', 'cathepsin l', 'host', 'basc', 'mpro', 'glycoprotein', 'cd13', 'nsp15', 'ccr5', 'zbcov', 'light', 'ddx1', 'aim', 'envelope', 'ifn', 'nl63', 'ga', 'homology', 'antibody', 'dpp4', 'orfx', 'damage', 'n protein', 'ntd', 'protein', 'interferon', 'plpro', 'nlrp3', 's protein', 'spike protein', 'alt', 'rr', 'platelet', 'damage', 'interferon', 'plasma', 'antigen', 

In [ ]:


# queries = [
#     ## Query1: What are the genes/proteins related to Covid-19
#    [
#        """MATCH (n)-[r:gene_disease]->(m) 
# where m.id in ['covid-19', 'coronavirus', 'sars-cov', 'sars', 'covs', 'severe acute respiratory syndrome']  or n.id in ['covid-19', 'coronavirus', 'sars-cov', 'sars', 'covs', 'severe acute respiratory syndrome']
# RETURN n, r, m""",
#     """MATCH (n)-[r:disease_gene]->(m) 
# where m.id in ['covid-19', 'coronavirus', 'sars-cov', 'sars', 'covs', 'severe acute respiratory syndrome']  or n.id in ['covid-19', 'coronavirus', 'sars-cov', 'sars', 'covs', 'severe acute respiratory syndrome']
# RETURN n, r, m"""
#    ],
#     ## Query2: What species transmit the covid-19
#     [
#        """MATCH (n)-[r:disease_species]->(m) 
# where m.id in ['covid-19', 'coronavirus', 'sars-cov', 'sars', 'covs', 'severe acute respiratory syndrome']  or n.id in ['covid-19', 'coronavirus', 'sars-cov', 'sars', 'covs', 'severe acute respiratory syndrome']
# RETURN n, r, m """ 
#     ],
#     ## Query3: what are symptoms of the covid-19
#     [
#         """MATCH (n)-[r:disease_symptom]->(m) 
# where m.id in ['covid-19', 'coronavirus', 'sars-cov', 'sars', 'covs', 'severe acute respiratory syndrome']  or n.id in ['covid-19', 'coronavirus', 'sars-cov', 'sars', 'covs', 'severe acute respiratory syndrome']
# RETURN n, r, m """,
#         """MATCH (n)-[r:symptom_disease]->(m) 
# where m.id in ['covid-19', 'coronavirus', 'sars-cov', 'sars', 'covs', 'severe acute respiratory syndrome']  or n.id in ['covid-19', 'coronavirus', 'sars-cov', 'sars', 'covs', 'severe acute respiratory syndrome']
# RETURN  n, r, m"""
#     ],
#     ## Query4: what are the possible therapeutic procedure of covid-19??
#     [
#         """MATCH (n)-[r:disease_treat_procedure]->(m) 
# where m.id in ['covid-19', 'coronavirus', 'sars-cov', 'sars', 'covs', 'severe acute respiratory syndrome']  or n.id in ['covid-19', 'coronavirus', 'sars-cov', 'sars', 'covs', 'severe acute respiratory syndrome']
# RETURN  n, r, m""",
#         """MATCH (n)-[r:treat_procedure_disease]->(m) 
# where m.id in ['covid-19', 'coronavirus', 'sars-cov', 'sars', 'covs', 'severe acute respiratory syndrome']  or n.id in ['covid-19', 'coronavirus', 'sars-cov', 'sars', 'covs', 'severe acute respiratory syndrome']
# RETURN  n, r, m """
#     ],
#     ## Query5: What are potential drugs to treat COVID-19?
#     [
#         """MATCH (n)-[r:drug_disease]->(m) 
# where m.id in ['covid-19', 'coronavirus', 'sars-cov', 'sars', 'covs', 'severe acute respiratory syndrome']  or n.id in ['covid-19', 'coronavirus', 'sars-cov', 'sars', 'covs', 'severe acute respiratory syndrome']
# RETURN  n, r, m""",
#         """MATCH (n)-[r:disease_drug]->(m) 
# where m.id in ['covid-19', 'coronavirus', 'sars-cov', 'sars', 'covs', 'severe acute respiratory syndrome']  or n.id in ['covid-19', 'coronavirus', 'sars-cov', 'sars', 'covs', 'severe acute respiratory syndrome']
# RETURN  n, r, m"""
#     ],
#     ## Query6: What are related diseases of Covid-19
#     [
#         """MATCH (n)-[r:disease_disease]->(m) 
# where m.id in ['covid-19', 'coronavirus', 'sars-cov', 'sars', 'covs', 'severe acute respiratory syndrome']  or n.id in ['covid-19', 'coronavirus', 'sars-cov', 'sars', 'covs', 'severe acute respiratory syndrome']
# RETURN n, r, m"""
#     ]
# ]
# # session.run(cmd)
# conn.query("""MATCH (n)-[r:gene_disease]->(m) where m.id in ['covid-19', 'coronavirus', 'sars-cov', 'sars', 'covs', 'severe acute respiratory syndrome'] or n.id in ['covid-19', 'coronavirus', 'sars-cov', 'sars', 'covs', 'severe acute respiratory syndrome'] RETURN n, r, m""")
# # top_cat_df = pd.DataFrame([dict(_) for _ in conn.query(query)])
# # top_cat_df

In [7]:
# Loading data
re_dataset = requests.get('https://raw.githubusercontent.com/HuyenNguyenHelen/CORD-19-KG/master/Data/all-final-cleaned-triples_3.csv').content
dataset = pd.read_csv(io.StringIO(re_dataset.decode('utf-8')))

dataset.drop(columns='Unnamed: 0', inplace=True)
# dataset = dataset[['subject','new_relation', 'object' ]]
dataset.head(5)
dataset_list = dataset.values.tolist()

# Loading data to neo4j
transaction_execution_commands=[]
for i in dataset_list :
    neo4j_create_statemenet = "create (t:triples {subject:" + str(i[0]) +", relation:  " + str(i[1]) +", object: " + str(i[2]) + "})"
    print(neo4j_create_statemenet)
    transaction_execution_commands.append(neo4j_create_statemenet)
    
def execute_transactions(transaction_execution_commands):
#     data_base_connection = GraphDatabase.driver(uri = "bolt://localhost:7687", auth=("neo4j", "password"))
    session = driver.session()    
    for i in transaction_execution_commands:
        session.run(i)
        
# create a neo4j session in python
session = driver.session()
# store all the records(including nodes & relationships) in a list
records = list(session.run("Match ((n)-[r]->(m)) return n,r,m"))


execute_transactions(transaction_execution_commands)

create (t:triples {subject:dysfunction, relation:  disease_species, object: child})
create (t:triples {subject:et dysfunction, relation:  disease_species, object: child})
create (t:triples {subject:rsv, relation:  disease_disease, object: virus})
create (t:triples {subject:treatment, relation:  treat_procedure_species, object: child})
create (t:triples {subject:urgency, relation:  disease_disease, object: virus})
create (t:triples {subject:chloroquine, relation:  drug_gene, object: base})
create (t:triples {subject:virus, relation:  disease_disease, object: virus})
create (t:triples {subject:step, relation:  gene_gene, object: endosomes})
create (t:triples {subject:chloroquine, relation:  drug_drug, object: chloroquine})
create (t:triples {subject:drug, relation:  drug_gene, object: viral nucleotidyl transferase})
create (t:triples {subject:chloroquine, relation:  drug_symptom, object: weak})
create (t:triples {subject:rna, relation:  disease_treat_procedure, object: extracted})
create

create (t:triples {subject:disease, relation:  disease_gene, object: toll})
create (t:triples {subject:extracorporeal life support, relation:  treat_procedure_species, object: patient})
create (t:triples {subject:life support, relation:  treat_procedure_species, object: patient})
create (t:triples {subject:bark, relation:  gene_disease, object: bronchitis})
create (t:triples {subject:bark, relation:  gene_treat_procedure, object: treatment})
create (t:triples {subject:hepatotoxicity, relation:  disease_drug, object: drug})
create (t:triples {subject:hbgas, relation:  gene_disease, object: infection})
create (t:triples {subject:noroviruses, relation:  disease_gene, object: hbgas})
create (t:triples {subject:carbohydrate, relation:  drug_gene, object: fut2 susceptibility allele})
create (t:triples {subject:fut2 enzyme, relation:  gene_drug, object: carbohydrate})
create (t:triples {subject:h type 3, relation:  gene_drug, object: ley})
create (t:triples {subject:influenza virus, relation:

create (t:triples {subject:no, relation:  drug_disease, object: encephalitis})
create (t:triples {subject:no, relation:  drug_disease, object: influenza infection})
create (t:triples {subject:treatment, relation:  treat_procedure_drug, object: pioglitazone})
create (t:triples {subject:pneumonitis, relation:  disease_gene, object: no})
create (t:triples {subject:treatment, relation:  treat_procedure_disease, object: pneumonitis})
create (t:triples {subject:hiv infection, relation:  disease_disease, object: injury})
create (t:triples {subject:immunosuppression, relation:  disease_species, object: cat})
create (t:triples {subject:neuroinflammation, relation:  disease_treat_procedure, object: induction})
create (t:triples {subject:lentivirus infection, relation:  disease_disease, object: axonal injury})
create (t:triples {subject:lentivirus infection, relation:  disease_disease, object: injury})
create (t:triples {subject:ccl2, relation:  gene_disease, object: virus})
create (t:triples {su

create (t:triples {subject:treatment, relation:  treat_procedure_drug, object: mycophenolate mofetil})
create (t:triples {subject:treatment, relation:  treat_procedure_drug, object: mycophenolate})
create (t:triples {subject:he, relation:  disease_disease, object: leucopenia})
create (t:triples {subject:treatment, relation:  treat_procedure_drug, object: prednisone})
create (t:triples {subject:he, relation:  disease_treat_procedure, object: therapy})
create (t:triples {subject:leucopenia, relation:  disease_disease, object: pancreatitis})
create (t:triples {subject:he, relation:  disease_drug, object: oseltamivir})
create (t:triples {subject:she, relation:  gene_disease, object: respiratory failure})
create (t:triples {subject:respiratory distress, relation:  disease_disease, object: bronchitis})
create (t:triples {subject:distress syndrome, relation:  disease_disease, object: covid-19})
create (t:triples {subject:respiratory distress syndrome, relation:  disease_disease, object: covid

create (t:triples {subject:oseltamivir, relation:  drug_species, object: patient})
create (t:triples {subject:antibiotic therapy, relation:  treat_procedure_drug, object: oseltamivir})
create (t:triples {subject:he, relation:  disease_treat_procedure, object: detection})
create (t:triples {subject:cns lesion, relation:  disease_symptom, object: spasticity})
create (t:triples {subject:cns lesion, relation:  disease_disease, object: weakness})
create (t:triples {subject:antibody, relation:  gene_gene, object: cut})
create (t:triples {subject:env, relation:  gene_treat_procedure, object: detected})
create (t:triples {subject:infection, relation:  disease_disease, object: tract infection})
create (t:triples {subject:infection, relation:  disease_disease, object: respiratory tract infection})
create (t:triples {subject:respiratory syndrome, relation:  disease_disease, object: viral pneumonia})
create (t:triples {subject:syndrome, relation:  disease_disease, object: viral pneumonia})
create 

...

create (t:triples {subject:opportunistic infection, relation:  disease_disease, object: mycobacteriosis})
create (t:triples {subject:cutaneous infection, relation:  disease_species, object: cattle})
create (t:triples {subject:mycobacterial infection, relation:  disease_disease, object: mycobacteriosis})
create (t:triples {subject:generalized lymphadenopathy, relation:  disease_treat_procedure, object: clipping})
create (t:triples {subject:cutaneous infection, relation:  disease_disease, object: mycobacteriosis})
create (t:triples {subject:lymphadenopathy, relation:  disease_treat_procedure, object: clipping})
create (t:triples {subject:infection, relation:  disease_disease, object: mycobacteriosis})
create (t:triples {subject:skin disease, relation:  disease_treat_procedure, object: clipping})
create (t:triples {subject:mycobacterial infection, relation:  disease_species, object: cattle})
create (t:triples {subject:panniculitis, relation:  disease_disease, object: systemic disease})
cr

create (t:triples {subject:disease, relation:  disease_species, object: dairy cattle})
create (t:triples {subject:stertor, relation:  symptom_disease, object: acute rhinitis})
create (t:triples {subject:stertor, relation:  symptom_disease, object: rhinitis})
create (t:triples {subject:infection, relation:  disease_disease, object: hemorrhagic septicemia})
create (t:triples {subject:mastitis, relation:  disease_disease, object: acute})
create (t:triples {subject:inflammation, relation:  disease_gene, object: red})
create (t:triples {subject:metritis, relation:  disease_species, object: cow})
create (t:triples {subject:pneumonic, relation:  disease_disease, object: mycoplasma})
create (t:triples {subject:alveolitis, relation:  disease_disease, object: bronchiolitis})
create (t:triples {subject:tuberculosis, relation:  disease_species, object: human})
create (t:triples {subject:tuberculosis, relation:  disease_species, object: m. bovis})
create (t:triples {subject:distress syndrome, relat

create (t:triples {subject:drug therapy, relation:  treat_procedure_treat_procedure, object: transplantation})
create (t:triples {subject:csa, relation:  drug_gene, object: all})
create (t:triples {subject:remdesivir, relation:  drug_treat_procedure, object: administered intravenously})
create (t:triples {subject:spike protein, relation:  gene_gene, object: e2})
create (t:triples {subject:s1 subunit, relation:  gene_gene, object: ectodomain})
create (t:triples {subject:s gene, relation:  gene_gene, object: past})
create (t:triples {subject:protein, relation:  gene_treat_procedure, object: intubation})
create (t:triples {subject:radiotherapy, relation:  treat_procedure_disease, object: disease})
create (t:triples {subject:reduction, relation:  treat_procedure_treat_procedure, object: destruction})
create (t:triples {subject:effusion, relation:  disease_disease, object: pulmonary consolidation})
create (t:triples {subject:presence, relation:  treat_procedure_treat_procedure, object: thor

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



CypherSyntaxError: {code: Neo.ClientError.Statement.SyntaxError} {message: Variable `dysfunction` not defined (line 1, column 28 (offset: 27))
"create (t:triples {subject:dysfunction, relation:  disease_species, object: child})"
                            ^}

In [ ]:
def create_friend_of(tx, name, friend):
    tx.run("MATCH (a:Person) WHERE a.name = $name "
           "CREATE (a)-[:KNOWS]->(:Person {name: $friend})",
           name=name, friend=friend)

with driver.session() as session:
    session.write_transaction(create_friend_of, "Alice", "Bob")

with driver.session() as session:
    session.write_transaction(create_friend_of, "Alice", "Carl")

driver.close()

In [ ]:
for i in transaction_list:
    neo4j_create_statemenet = "create (t:Transaction {transaction_id:" + str(i[0]) +", vendor_number:  " + str(i[1]) +", transaction_amount: " + str(i[2]) +", transaction_type: '" + str(i[3]) + "'})"
    transaction_execution_commands.append(neo4j_create_statemenet)